# Libraries

In [1]:
# !pip install kafka-python
# !pip install confluent-kafka

In [2]:
import pandas as pd 
import json
import random 
import time
import hashlib


from kafka import KafkaProducer
from confluent_kafka import Producer
import socket
import json
import os

from kafka_auth import conf



# Purchase Simulation 

In [3]:
# List of cities - Used for categorizing user locations.
cities = ['Guatemala', 'Progreso', 'Peten', 'Izabal', 'Sacatepequez']

# List of online payment methods - Includes 'Credit_card' and 'Paypal'.
payment_online = ['Credit_card', 'Paypal']

# List of in-store payment methods - Represents physical store payment options.
payment_store = ['Cash', 'NexaBanco', 'Transferencia', 'Credit_card']

# List of user traffic sources - Contains sources like social media and influencers.
source = ['Facebook', 'Instagram', 'Organic', 'Twitter', 'Influencer_1', 'Influencer_2', 'Influencer_3', 'Influencer_4']

# List of purchase statuses - Indicates the status of a purchase transaction.
status_purchase = ['COMPLETED', 'FAILED_CHECKOUT', 'FAILED_API_RESPONSE', 'INSUFFICIENT_FUNDS', 'COMPLETED', 'COMPLETED', 'COMPLETED', 'COMPLETED', 'COMPLETED', 'COMPLETED', 'FAILED_API_RESPONSE', 'INSUFFICIENT_FUNDS', 'USER_ERROR', 'FRAUD', 'COMPLETED', 'COMPLETED', 'COMPLETED']


In [4]:
# Coordinates of 5 departments of Guatemala
guate_coords = [(14.583433719731175, -90.54504814981065), (14.650697781115896, -90.54347326760755), (14.551813110062895, -90.4536564836989)]
pro_coords = [(14.747716452097745, -90.11598064639617), (14.923123389835915, -90.01637445881771)]
pet_coords = [(16.199295697554618, -89.44288359648083), (16.912352332743886, -89.91634392561033), (16.97082962261178, -89.91160163056682)]
iza_coords = [(15.254832206786691, -89.09696966551803), (15.662598645388154, -89.01134914632459), (15.696427120923515, -88.58694351197549)]
sac_coords = [(14.531109705961676, -90.75143141168198), (14.63344752887805, -90.67879049389634), (14.613376075028672, -90.65475837333969)]

In [5]:
# Function to determine payment method, status, and order type based on source
def get_pay_method(source, status_purchase, payment_online, payment_store):
    # If the source is 'Organic', use a payment method from 'payment_store'.
    if source == 'Organic':
        payment = random.choice(payment_store)
        status = 'COMPLETED'  # Assume completed status for organic source.
        order_type = 'STORE'  # Order type is for in-store purchases.
    # If the source is not 'Organic', use an online payment method and random status.
    elif source != 'Organic':
        payment = random.choice(payment_online)
        status = random.choice(status_purchase)  # Randomly select a status.
        order_type = 'ONLINE'  # Order type is for online purchases.

    return payment, status, order_type

# Function to get coordinates for a given city
def get_coords(city):
    # Determine coordinates based on the specified city.
    if city == 'Guatemala':
        coords = random.choice(guate_coords)
    elif city == 'Progreso':
        coords = random.choice(sac_coords)
    elif city == 'Peten':
        coords = random.choice(pet_coords)
    elif city == 'Izabal':
        coords = random.choice(pro_coords)
    elif city == 'Sacatepequez':
        coords = random.choice(iza_coords)

    return coords


In [6]:
pay = get_pay_method('Organic',status_purchase,payment_online,payment_store)
print(pay)

('NexaBanco', 'COMPLETED', 'STORE')


In [7]:
pay[0]

'NexaBanco'

In [8]:
pay[1]

'COMPLETED'

In [9]:
random.choice(cities)

'Peten'

In [10]:
ciudad = random.choice(cities)
coordenadas = get_coords(ciudad)
print(f' Ciudad >> {ciudad}')
print(f' Coordenadas >> {coordenadas}')

 Ciudad >> Peten
 Coordenadas >> (16.199295697554618, -89.44288359648083)


In [11]:
# List of products for sale in .xlsx
df = pd.read_excel('ecomerce.xlsx')

In [12]:
df

PRODUCT_NAME   PRICING  COMISION     BRAND     CATEGORY
0    Laptop_Brand1_4GB   2565.0      0.20    Brand1      LAPTOPS
1    Laptop_Brand1_8GB   4845.0      0.25    Brand1      LAPTOPS
2   Laptop_Brand1_16GB   6650.0      0.30    Brand1      LAPTOPS
3   Laptop_Brand1_32GB   9120.0      0.35    Brand1       GAMING
4    Laptop_Brand2_4GB   2185.0      0.15    Brand2      LAPTOPS
5    Laptop_Brand2_8GB   3515.0      0.18    Brand2      LAPTOPS
6   Laptop_Brand2_16GB   7391.0      0.20    Brand2      LAPTOPS
7   Laptop_Brand2_32GB  13281.0      0.25    Brand2       GAMING
8    Laptop_Brand3_4GB   3515.0      0.20    Brand3      LAPTOPS
9    Laptop_Brand3_8GB   6078.1      0.28    Brand3      LAPTOPS
10  Laptop_Brand3_16GB   8852.1      0.30    Brand3      LAPTOPS
11  Laptop_Brand3_32GB  36098.1      0.40    Brand3       GAMING
12        Console_Xbox   3038.1      0.15     X_Box  VIDEO GAMES
13         Console_PS5   6764.0      0.30       PS5  VIDEO GAMES
14      Console_Switch   4273.1      0.20  Nintendo  VIDEO GAMES

# To Do's

*  Deploy a kafka Cluster on Confluent Cloud 
* Create a Kafka topic
* Test Python simulation Script

# Config Kafka Cluster

In [13]:
conf

{'bootstrap.servers': 'pkc-921jm.us-east-2.aws.confluent.cloud:9092',
 'security.protocol': 'SASL_SSL',
 'sasl.mechanisms': 'PLAIN',
 'sasl.username': 'HJ2SCLZLJMGU7CSW',
 'sasl.password': 'XRJaQPqWebtGdjLlzILv+DFW/jjE5PwFyQ5+G4E2psFxlpygAFBPtiptT/t1OzU1'}

In [14]:
# conf = ccloud_lib.read_ccloud_config('librdkafka.config')

# # Create Producer instance
# producer_conf = ccloud_lib.pop_schema_registry_params_from_config(conf)
# producer = Producer(producer_conf)

producer = Producer(conf)

# Send Message To Kafka Topic

In [15]:
delivered_records = 0  # Variable to keep track of the number of delivered records
topic = 'topic_Apache-KafkaDruidEC2'  # Kafka topic to which records will be produced

x = 1  # Initialization of the loop variable

data_purchase = []  # An empty list to potentially store purchase data

# Generate purchase data 
while(x > 0):
    
    # Get the current date and time
    date = pd.to_datetime('today').strftime("%Y-%m-%d %H:%M:%S")
    
    # Randomly select a product from a DataFrame
    product = df['PRODUCT_NAME '][random.randint(0,14)]
    
    # Retrieve pricing, commission, brand, and category information for the selected product
    pricing =  df[df['PRODUCT_NAME ']==product]['PRICING'].values[0]
    comision =  df[df['PRODUCT_NAME ']==product]['COMISION'].values[0]
    brand = df[df['PRODUCT_NAME ']==product]['BRAND'].values[0]
    category = df[df['PRODUCT_NAME ']==product]['CATEGORY'].values[0]
    
    # Randomly select a source
    source_temp = random.choice(source)
    
    # Determine the payment method, status, and order type using a custom function
    pay = get_pay_method(source_temp, status_purchase, payment_online, payment_store)
    
    # Randomly select a city
    city = random.choice(cities)
    
    # Create a dictionary representing a purchase record
    purchase = {
        'purchase_ID': str(hashlib.sha256(f"{x} {product} {pricing} {comision} {date} {source_temp} {pay[1]}".encode('utf-8')).hexdigest())[:15], 
        'Product_name': product,
        'Pricing': str(pricing),
        'Comision': str(comision),
        'Revenue': str(round(pricing * comision, 2)),
        'Payment_Mehtod': pay[0],
        'Status': pay[1],
        'Order_Type': pay[2],
        'City': city,
        'Location': str(get_coords(city)),
        'Latitud': str(get_coords(city)[0]),
        'Longitud': str(get_coords(city)[1]),
        'Source': source_temp,
        'Brand': brand,
        'Category': category,
        'Created_at': date
    }
    
    # Uncomment the following line to store purchase data in a list
    # data_purchase.append(pd.DataFrame(purchase))
    
    # Prepare a Kafka record with a key and value
    record_key = "Purchase_simulator"
    record_value =  json.dumps(purchase).encode('utf-8')
    
    # Print a message indicating the produced record
    print("Producing record: {}\t{}".format(record_key, record_value))
    
    # Produce the record to the Kafka topic using a Kafka producer
    producer.produce(topic, key=record_key, value=record_value)
    producer.poll(0)  # Poll to ensure the record is sent
    
    delivered_records += 1  # Increment the delivered record count
    x += 1  # Increment the loop variable
    
    # Sleep for a random duration before the next iteration
    # time.sleep(random.choice([0.5]))
    
# Flush the Kafka producer to ensure all records are sent
producer.flush()

# Print a summary of the produced records
print('\n')
print('\n')
print("{} messages were produced to topic {}!".format(delivered_records, topic))
print('\n')
print('\n')


Producing record: Purchase_simulator	b'{"purchase_ID": "c46ec1e57a8668d", "Product_name": "Laptop_Brand1_16GB", "Pricing": "6650.0", "Comision": "0.3", "Revenue": "1995.0", "Payment_Mehtod": "Credit_card", "Status": "COMPLETED", "Order_Type": "ONLINE", "City": "Izabal", "Location": "(14.923123389835915, -90.01637445881771)", "Latitud": "14.747716452097745", "Longitud": "-90.01637445881771", "Source": "Influencer_1", "Brand": "Brand1", "Category": "LAPTOPS", "Created_at": "2023-10-01 02:10:38"}'
Producing record: Purchase_simulator	b'{"purchase_ID": "6da6232b4803fe5", "Product_name": "Laptop_Brand2_16GB", "Pricing": "7391.0", "Comision": "0.2", "Revenue": "1478.2", "Payment_Mehtod": "Credit_card", "Status": "COMPLETED", "Order_Type": "ONLINE", "City": "Progreso", "Location": "(14.531109705961676, -90.75143141168198)", "Latitud": "14.531109705961676", "Longitud": "-90.67879049389634", "Source": "Influencer_3", "Brand": "Brand2", "Category": "LAPTOPS", "Created_at": "2023-10-01 02:10:38"}

KeyboardInterrupt: 